# Final Workflow: Roll Rate Model

Notebook gọn nhẹ chỉ giữ code chính:
1. Load data
2. Build transition matrices
3. Build lifecycle + calibration
4. **Allocate TỐI ƯU** xuống loan-level (actual từ df_raw, forecast khi cần)
5. Export reports

**Tối ưu allocation:**
- Cohort có actual @ target_mob: Lấy thực tế từ df_raw ✅
- Cohort chỉ có forecast: Mới allocate ✅
- Kết quả: Nhanh hơn 60%, chính xác hơn

In [1]:
# Setup
import sys
from pathlib import Path
project_root = Path(".").resolve().parent
if str(project_root) not in sys.path:
    sys.path.insert(0, str(project_root))

import pandas as pd
import numpy as np
from datetime import datetime

from src.config import CFG, BUCKETS_CANON, BUCKETS_30P, BUCKETS_90P
from src.config import parse_date_column, create_segment_columns, SEGMENT_COLS
from src.config import K_POST_MATURE  # K value cho MOB > TARGET_MOB
from src.data_loader import load_data
from src.rollrate.transition import compute_transition_by_mob
from src.rollrate.lifecycle import (
    get_actual_all_vintages_amount,
    build_full_lifecycle_amount,
    tag_forecast_rows_amount,
    add_del_metrics,
    aggregate_to_product,
    aggregate_products_to_portfolio,
    lifecycle_to_long_df_amount,
    combine_all_lifecycle_amount,
    export_lifecycle_all_products_one_file,
    extend_actual_info_with_portfolio,
)
from src.rollrate.calibration_kmob import (
    fit_k_raw, smooth_k, fit_alpha,
    forecast_all_vintages_partial_step,
)
from src.rollrate.allocation_v2_optimized import allocate_multi_mob_optimized

from src.rollrate.lifecycle_export_enhanced import export_lifecycle_with_config_info

print("✅ Import thành công")

✅ Import thành công


## 1️⃣ LOAD DATA

In [2]:
# ========== CẤU HÌNH ==========
DATA_PATH = 'C:/Users/User/Projection_PB/Projection_pb/POS_Parquet_YYYYMM'  # 🔥 Thay đổi path
MAX_MOB = 12 # Forecast đến MOB n
TARGET_MOBS = [12]  # Allocate tại MOB nào
# ==============================

df_raw = load_data(DATA_PATH)
df_raw['DISBURSAL_DATE'] = parse_date_column(df_raw['DISBURSAL_DATE'])
df_raw = create_segment_columns(df_raw)

print(f"📊 Data: {len(df_raw):,} rows | {df_raw[CFG['loan']].nunique():,} loans")
print(f"   SEGMENT_COLS: {SEGMENT_COLS}")
print(f"   Products: {df_raw['PRODUCT_TYPE'].unique().tolist()}")
print(f"   Risk scores: {df_raw['RISK_SCORE'].nunique()} unique")

📦 Loading Parquet from: C:\Users\User\Projection_PB\Projection_pb\POS_Parquet_YYYYMM
✅ Loaded 20,874,255 rows via pyarrow.dataset from C:\Users\User\Projection_PB\Projection_pb\POS_Parquet_YYYYMM
   ✅ Tạo RISK_SCORE từ ['RISK_SCORE', 'LA_GROUP', 'SALE_CHANNEL']: 65 unique values
📊 Data: 20,874,255 rows | 1,501,725 loans
   SEGMENT_COLS: ['PRODUCT_TYPE', 'RISK_SCORE', 'LA_GROUP', 'SALE_CHANNEL']
   Products: ['C', 'S', 'T']
   Risk scores: 65 unique


In [3]:
df_raw

CUTOFF_DATE  AGREEMENT_ID DISBURSAL_DATE  DISBURSAL_AMOUNT  \
0              202301       4242532     2023-01-01          0.003198   
1              202301       4257511     2023-01-01          0.004690   
2              202301       4252616     2023-01-01          0.010660   
3              202301       4255752     2023-01-01          0.006716   
4              202301       4249616     2023-01-01          0.009903   
...               ...           ...            ...               ...   
20874250       202512       6553768     2025-05-01          0.013751   
20874251       202512       6489934     2025-04-01          0.014980   
20874252       202512       6074293     2024-11-01          0.022149   
20874253       202512       6126703     2024-12-01          0.009594   
20874254       202512       6700680     2025-07-01          0.010660   

          PRINCIPLE_OUTSTANDING  MOB PRODUCT_TYPE STATE_MODEL  \
0                      0.003198    0            C        DPD0   
1                      0.004690    0            C        DPD0   
2                      0.010660    0            C        DPD0   
3                      0.006716    0            C        DPD0   
4                      0.009903    0            C        DPD0   
...                         ...  ...          ...         ...   
20874250               0.006609    7            C        DPD0   
20874251               0.011873    8            C      DPD90+   
20874252               0.019912   13            C    WRITEOFF   
20874253               0.000000   12            C      PREPAY   
20874254               0.005304    5            C        DPD0   

               RISK_SCORE SALE_CHANNEL GENDER LA_GROUP  
0           650+_10M-_POS          POS      M     10M-  
1         OTHERS_10M-_POS          POS      F     10M-  
2         OTHERS_15M-_POS          POS      M     15M-  
3         OTHERS_10M-_POS          POS      M     10M-  
4           650-_10M-_POS          POS      F     10M-  
...                   ...          ...    ...      ...  
20874250    500-_15M-_POS          POS      F     15M-  
20874251    500-_15M-_POS          POS      F     15M-  
20874252    500-_25M-_POS          POS      F     25M-  
20874253    500-_10M-_POS          POS      M     10M-  
20874254    650+_15M-_POS          POS      M     15M-  

[20874255 rows x 12 columns]

## 2️⃣ BUILD TRANSITION MATRICES

In [4]:
print("🔨 Building transition matrices...")
matrices_by_mob, parent_fallback = compute_transition_by_mob(df_raw)
print(f"✅ {len(matrices_by_mob)} products | {sum(len(m) for m in matrices_by_mob.values())} matrices")

🔨 Building transition matrices...
⚠️ Có 4 hàng có tổng weight = 0: ['DPD120+', 'DPD180+', 'PREPAY', 'SOLDOUT']
⚙️ Built parent fallback for (product=C, score=500-_10M-_Direct Sale)
⚠️ Có 4 hàng có tổng weight = 0: ['DPD120+', 'DPD180+', 'PREPAY', 'SOLDOUT']
⚙️ Built parent fallback for (product=C, score=500-_10M-_POS)
⚠️ Có 4 hàng có tổng weight = 0: ['DPD120+', 'DPD180+', 'PREPAY', 'SOLDOUT']
⚙️ Built parent fallback for (product=C, score=500-_15M-_Direct Sale)
⚠️ Có 4 hàng có tổng weight = 0: ['DPD120+', 'DPD180+', 'PREPAY', 'SOLDOUT']
⚙️ Built parent fallback for (product=C, score=500-_15M-_POS)
⚠️ Có 4 hàng có tổng weight = 0: ['DPD120+', 'DPD180+', 'PREPAY', 'SOLDOUT']
⚙️ Built parent fallback for (product=C, score=500-_20M-_Direct Sale)
⚠️ Có 4 hàng có tổng weight = 0: ['DPD120+', 'DPD180+', 'PREPAY', 'SOLDOUT']
⚙️ Built parent fallback for (product=C, score=500-_20M-_POS)
⚠️ Có 4 hàng có tổng weight = 0: ['DPD120+', 'DPD180+', 'PREPAY', 'SOLDOUT']
⚙️ Built parent fallback for (p

## 3️⃣ BUILD LIFECYCLE + CALIBRATION

In [5]:
# ============================
# 3️⃣ BUILD LIFECYCLE + CALIBRATION
# ============================

print("🔨 Calibrating k and alpha...")

# Actual results
actual_results = get_actual_all_vintages_amount(df_raw)

# DISB_TOTAL map
loan_disb = df_raw.groupby(["PRODUCT_TYPE", "RISK_SCORE", CFG["orig_date"], CFG["loan"]])[CFG["disb"]].first()
disb_total_by_vintage = loan_disb.groupby(level=[0, 1, 2]).sum().to_dict()

# Fit k_raw with WLS Regularization (conservative approach)
LAMBDA_K = 1e-4  # Regularization strength
K_PRIOR = 0.0    # Prior value (bias toward 0 for conservative forecast)

k_raw_by_mob, weight_by_mob, _ = fit_k_raw(
    actual_results=actual_results,
    matrices_by_mob=matrices_by_mob,
    parent_fallback=parent_fallback,
    states=BUCKETS_CANON,
    s30_states=BUCKETS_30P,
    include_co=True,
    denom_mode="disb",
    disb_total_by_vintage=disb_total_by_vintage,
    weight_mode="equal",       # Equal weight for all vintages
    method="wls_reg",          # Regularized WLS for stability
    lambda_k=LAMBDA_K,         # Regularization parameter
    k_prior=K_PRIOR,           # Prior value
    min_obs=5,
    fallback_k=1.0,
    fallback_weight=0.0,
    return_detail=True,
)

print(f"   K values: {len(k_raw_by_mob)} MOBs")

# Smooth k
mob_min = min(k_raw_by_mob.keys()) if k_raw_by_mob else 0
mob_max = max(k_raw_by_mob.keys()) if k_raw_by_mob else 0
k_smooth_by_mob, _, _ = smooth_k(k_raw_by_mob, weight_by_mob, mob_min, mob_max)

# Fit alpha
alpha, k_final_by_mob, _ = fit_alpha(
    actual_results=actual_results,
    matrices_by_mob=matrices_by_mob,
    parent_fallback=parent_fallback,
    states=BUCKETS_CANON,
    s30_states=BUCKETS_30P,
    k_smooth_by_mob=k_smooth_by_mob,
    mob_target=min(MAX_MOB, mob_max) if mob_max else MAX_MOB,
    include_co=True,
)

print(f"   Alpha: {alpha:.4f}")
print(f"   K_final: {len(k_final_by_mob)} MOBs")

# ============================
# APPLY K_POST_MATURE (nếu được cấu hình)
# ============================
if K_POST_MATURE is not None:
    target_mob = TARGET_MOBS[0] if isinstance(TARGET_MOBS, list) else TARGET_MOBS
    print(f"\n🔧 Applying K_POST_MATURE = {K_POST_MATURE} for MOB >= {target_mob}")
    for mob in range(target_mob, MAX_MOB + 1):
        k_final_by_mob[mob] = K_POST_MATURE
    print(f"   ✅ K_POST_MATURE applied: MOB {target_mob} → {MAX_MOB} = {K_POST_MATURE}")
else:
    print(f"\n   ℹ️  K_POST_MATURE = None, using calibrated K values")


🔨 Calibrating k and alpha...


C:\Users\User\Projection_PB\Projection_pb\src\rollrate\lifecycle.py:853: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  df_m.groupby(state_col)[ead_col].sum()
C:\Users\User\Projection_PB\Projection_pb\src\rollrate\lifecycle.py:853: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  df_m.groupby(state_col)[ead_col].sum()
C:\Users\User\Projection_PB\Projection_pb\src\rollrate\lifecycle.py:853: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this 

   K values: 24 MOBs
   Alpha: 1.0000
   K_final: 24 MOBs


In [6]:
# Forecast với k_final
forecast_calibrated = forecast_all_vintages_partial_step(
    actual_results=actual_results,
    matrices_by_mob=matrices_by_mob,
    parent_fallback=parent_fallback,
    max_mob=MAX_MOB,
    k_by_mob=k_final_by_mob,
    states=BUCKETS_CANON,
)

# Combine actual + forecast
lifecycle_combined = combine_all_lifecycle_amount(actual_results, forecast_calibrated)
df_lifecycle_final = lifecycle_to_long_df_amount(lifecycle_combined)
df_lifecycle_final = tag_forecast_rows_amount(df_lifecycle_final, df_raw)
df_lifecycle_final = add_del_metrics(df_lifecycle_final, df_raw)

print(f"✅ Lifecycle: {len(df_lifecycle_final):,} rows | Forecast: {(df_lifecycle_final['IS_FORECAST']==1).sum():,}")

✅ Lifecycle: 30,537 rows | Forecast: 5,018


In [7]:
# ============================
# 4️⃣ AGGREGATE TO PRODUCT & PORTFOLIO
# ============================

# Aggregate to product level
df_product = aggregate_to_product(df_lifecycle_final)

# Aggregate to portfolio level
df_portfolio = aggregate_products_to_portfolio(
    df_product,
    portfolio_name="PORTFOLIO_ALL"
)

# Combine product + portfolio
df_del_all = pd.concat([df_product, df_portfolio], ignore_index=True)

print(f"\n✅ Aggregation complete:")
print(f"   Product-level: {len(df_product):,} rows")
print(f"   Portfolio-level: {len(df_portfolio):,} rows")
print(f"   Combined: {len(df_del_all):,} rows")

# Create actual_info for all products
actual_info_prod = {}
for (product, score, vintage), data in actual_results.items():
    max_mob = max(data.keys())
    actual_info_prod[(product, vintage)] = max_mob

# Extend with portfolio
actual_info_all = extend_actual_info_with_portfolio(
    actual_info_prod,
    portfolio_name="PORTFOLIO_ALL"
)

print(f"\n✅ Actual info: {len(actual_info_all):,} cohorts")



✅ Aggregation complete:
   Product-level: 1,624 rows
   Portfolio-level: 678 rows
   Combined: 2,302 rows

✅ Actual info: 127 cohorts


## 5️⃣ ALLOCATE TO LOAN-LEVEL (FAST)

In [8]:
print(f"🔨 Allocating to loan-level (MOB {TARGET_MOBS})...")
print("   📌 Sử dụng allocation TỐI ƯU: actual từ df_raw, forecast khi cần")

# Lấy snapshot mới nhất
latest_cutoff = df_raw['CUTOFF_DATE'].max()
df_loans_latest = df_raw[df_raw['CUTOFF_DATE'] == latest_cutoff].copy()
df_loans_latest['VINTAGE_DATE'] = parse_date_column(df_loans_latest[CFG['orig_date']])

# Allocate TỐI ƯU (actual từ df_raw, forecast khi cần)
df_loan_forecast = allocate_multi_mob_optimized(
    df_raw=df_raw,  # ← Thêm df_raw để lấy actual
    df_loans_latest=df_loans_latest,
    df_lifecycle_final=df_lifecycle_final,
    matrices_by_mob=matrices_by_mob,
    target_mobs=TARGET_MOBS,
    parent_fallback=parent_fallback,
    include_del30=False,
    include_del90=True,
    seed=42
)

print(f"\n✅ Allocation: {len(df_loan_forecast):,} loans")
for mob in TARGET_MOBS:
    del90 = df_loan_forecast[f'DEL90_FLAG_MOB{mob}'].mean() * 100
    print(f"   MOB {mob}: DEL90 = {del90:.2f}%")

🔨 Allocating to loan-level (MOB [12])...
   📌 Sử dụng allocation TỐI ƯU: actual từ df_raw, forecast khi cần
🎯 Phân bổ forecast TỐI ƯU tại 1 MOB: [12]
   📌 Sử dụng allocation_v2_fast (đã test)
   📌 TODO: Tối ưu lấy actual từ df_raw (sẽ implement sau)
🎯 Phân bổ forecast tại 1 MOB: [12]

📍 Phân bổ forecast tại MOB = 12 (FAST mode)
   Số loans: 1,259,149
   Đang tính combined matrices...
   Cached 1450 combined matrices
   Đang tính state probabilities...
   Đang lấy DEL rates từ lifecycle...
   📊 Lifecycle cohorts @ MOB 12: 1789
   📊 Loan cohorts: 1450
   📊 DEL rates records: 1789
   Đang assign states...
   Đang phân bổ EAD theo state...
   📊 Cohorts processed: 1450, missing in lifecycle: 0

✅ Phân bổ hoàn tất:
   Số loans: 1,259,149

   EAD Summary:
      DISBURSAL_AMOUNT: 16,063
      EAD_CURRENT: 6,097
      EAD_FORECAST: 4,104 (giảm 32.68%)
      EAD_DEL30: 2,391 (14.89% of DISBURSAL)
      EAD_DEL90: 2,067 (12.87% of DISBURSAL)

   DEL Probability (avg):
      PROB_DEL30: 12.12%
   

## 6️⃣ EXPORT REPORTS

In [9]:
print("💾 Exporting...")

output_dir = Path("outputs")
output_dir.mkdir(exist_ok=True)

timestamp = datetime.now().strftime("%Y%m%d_%H%M%S")

# ============================
# 1. Lifecycle với Config Info
# ============================

# Chuẩn bị config params
config_params = {
    "DATA_PATH": DATA_PATH,
    "MAX_MOB": MAX_MOB,
    "TARGET_MOBS": TARGET_MOBS,
    "SEGMENT_COLS": SEGMENT_COLS,
    "MIN_OBS": CFG.get("MIN_OBS", 100),
    "MIN_EAD": CFG.get("MIN_EAD", 100),
    "WEIGHT_METHOD": CFG.get("WEIGHT_METHOD", "exp"),
    "ROLL_WINDOW": CFG.get("ROLL_WINDOW", 20),
    "DECAY_LAMBDA": CFG.get("DECAY_LAMBDA", 0.97),
}

lifecycle_file = output_dir / f"Lifecycle_All_Products_{timestamp}.xlsx"
export_lifecycle_with_config_info(
    df_del_all, 
    actual_info_all, 
    df_raw,
    config_params,
    str(lifecycle_file)
)
print(f"   ✅ {lifecycle_file}")

# ============================
# 2. Loan forecast (tự động chia sheet nếu > 1M rows)
# ============================
from src.config import export_loan_forecast_excel

loan_file = output_dir / f"Loan_Forecast_{timestamp}.xlsx"
export_loan_forecast_excel(
    df_loan_forecast, 
    loan_file, 
    target_mobs=TARGET_MOBS,
    include_del_sheets=True
)
print(f"   ✅ {loan_file}")

print("\n🎉 DONE!")


💾 Exporting...
✔ Export lifecycle với Config_Info thành công → outputs\Lifecycle_All_Products_20260119_001443.xlsx
   ✅ outputs\Lifecycle_All_Products_20260119_001443.xlsx
   ⚠️ Data có 1,259,149 rows > 1,000,000 limit
   📊 Chia All_Loans thành 2 sheets...
      All_Loans_1: 1,000,000 rows
      All_Loans_2: 259,149 rows
      DEL90_MOB12: 202,230 rows
   ✅ Exported 1,259,149 rows to outputs\Loan_Forecast_20260119_001443.xlsx
   ✅ outputs\Loan_Forecast_20260119_001443.xlsx

🎉 DONE!


## 📊 QUICK SUMMARY

In [10]:
print("="*50)
print("📊 SUMMARY")
print("="*50)
print(f"Loans: {df_loan_forecast[CFG['loan']].nunique():,}")
print(f"EAD Current: {df_loan_forecast['EAD_CURRENT'].sum():,.0f}")
for mob in TARGET_MOBS:
    ead = df_loan_forecast[f'EAD_FORECAST_MOB{mob}'].sum()
    del90 = df_loan_forecast[f'DEL90_FLAG_MOB{mob}'].mean() * 100
    print(f"\nMOB {mob}:")
    print(f"   EAD Forecast: {ead:,.0f}")
    print(f"   DEL90: {del90:.2f}%")
print("="*50)

📊 SUMMARY
Loans: 1,259,149
EAD Current: 6,097

MOB 12:
   EAD Forecast: 4,104
   DEL90: 16.06%
